In [18]:
import sys
sys.path.insert(0, './animals_detection')
from models.common import DetectMultiBackend
from utils.dataloaders import IMG_FORMATS, VID_FORMATS, LoadImages, LoadStreams
from utils.general import (LOGGER, check_file, check_img_size, check_imshow, check_requirements, colorstr, cv2,
                           increment_path, non_max_suppression, print_args, scale_coords, strip_optimizer, xyxy2xywh, xywh2xyxy)
from utils.plots import Annotator, colors, save_one_box
from utils.torch_utils import select_device, time_sync
from utils.metrics import box_iou

import json
import torch
import os

In [2]:
conf_thres=0.25  # confidence threshold
iou_thres=0.45  # NMS IOU threshold
max_det=1000

imgsz = (640, 640)
device = "0"
weights = "animals_detection/pig_detection/def_yolo5m_masked_union_hard_5_epochs/weights/best.pt"
data = "animals_detection/data/pigs_detection_yolo_masked_union_hard_dataset.yaml"
source = "animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/"
with open("detection_annotations.json", 'r') as f:
    annotations = json.load(f)
annotations = {img["frame_filename"]: img for img in annotations}
device = select_device(device)
model = DetectMultiBackend(weights, device=device, dnn=False, data=data, fp16=False)
stride, names, pt = model.stride, model.names, model.pt
imgsz = check_img_size(imgsz, s=stride)  # check image size

dataset = LoadImages(source, img_size=imgsz, stride=stride, auto=pt)
bs = 1  # batch_size
vid_path, vid_writer = [None] * bs, [None] * bs



YOLOv5 🚀 2022-6-13 Python-3.8.13 torch-1.11.0+cu102 CUDA:0 (GeForce RTX 2080, 7979MiB)

Fusing layers... 
Model summary: 290 layers, 20865057 parameters, 0 gradients


In [3]:
# Run inference
preds = {}
model.warmup(imgsz=(1 if pt else bs, 3, *imgsz))  # warmup
dt, seen = [0.0, 0.0, 0.0], 0
for path, im, im0s, vid_cap, s in dataset:
    t1 = time_sync()
    im = torch.from_numpy(im).to(device)
    im = im.half() if model.fp16 else im.float()  # uint8 to fp16/32
    im /= 255  # 0 - 255 to 0.0 - 1.0
    if len(im.shape) == 3:
        im = im[None]  # expand for batch dim
    t2 = time_sync()
    dt[0] += t2 - t1
    gt = annotations[path.split('/')[-1]]
   
    # Inference
    pred = model(im, augment=False, visualize=False)
    t3 = time_sync()
    dt[1] += t3 - t2

    # NMS
    pred = non_max_suppression(pred, conf_thres, iou_thres, max_det=max_det)
    dt[2] += time_sync() - t3

    # Second-stage classifier (optional)
    # pred = utils.general.apply_classifier(pred, classifier_model, im, im0s)

    # Process predictions
    for i, det in enumerate(pred):  # per image
        seen += 1
        p, im0 = path, im0s.copy()

        s += '%gx%g ' % im.shape[2:]  # print string
        gn = torch.tensor(im0.shape)[[1, 0, 1, 0]]  # normalization gain whwh
        imc = im0 
        annotator = Annotator(im0, line_width=10, example=str(names))
        pred_boxes = []
        if len(det):
            # Rescale boxes from img_size to im0 size
            det[:, :4] = scale_coords(im.shape[2:], det[:, :4], im0.shape).round()

            gt_boxes = torch.Tensor([[box['bbox']['x'], box['bbox']['y'],
                         box['bbox']['x'] + box['bbox']['width'],
                         box['bbox']['y'] + box['bbox']['height']] for box in gt['bboxes']])
            gt_ids = [box['id'] for box in gt['bboxes']]
            # Write results
            for *xyxy, conf, cls in reversed(det):
                iou = box_iou(torch.Tensor(xyxy).view(1, 4), gt_boxes)[0]
                max_iou = torch.argmax(iou)
                if iou[max_iou] < iou_thres:
                    continue
               

                xywh = (xyxy2xywh(torch.tensor(xyxy).view(1, 4))).view(-1).tolist()
                pred_boxes.append([xywh] + [conf.item()] +[gt_ids[max_iou]])
                if True:  # Add bbox to image
                    c = int(gt_ids[max_iou])  # integer class
                    label = gt_ids[max_iou]
                    annotator.box_label(xyxy, label, color=colors(c, True))

        preds[p] = pred_boxes
        # Stream results
        im0 = annotator.result()
#         if True:
#             cv2.imshow(source, im0)
#             cv2.waitKey(1)  # 1 millisecond

        # Save results (image with detections)
#         if save_img:
#             if dataset.mode == 'image':
#                 cv2.imwrite(save_path, im0)
#             else:  # 'video' or 'stream'
#                 if vid_path[i] != save_path:  # new video
#                     vid_path[i] = save_path
#                     if isinstance(vid_writer[i], cv2.VideoWriter):
#                         vid_writer[i].release()  # release previous video writer
#                     if vid_cap:  # video
#                         fps = vid_cap.get(cv2.CAP_PROP_FPS)
#                         w = int(vid_cap.get(cv2.CAP_PROP_FRAME_WIDTH))
#                         h = int(vid_cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
#                     else:  # stream
#                         fps, w, h = 30, im0.shape[1], im0.shape[0]
#                     save_path = str(Path(save_path).with_suffix('.mp4'))  # force *.mp4 suffix on results videos
#                     vid_writer[i] = cv2.VideoWriter(save_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (w, h))
#                 vid_writer[i].write(im0)

    # Print time (inference-only)
    LOGGER.info(f'{s}Done. ({t3 - t2:.3f}s)')

# Print results
t = tuple(x / seen * 1E3 for x in dt)  # speeds per image
LOGGER.info(f'Speed: %.1fms pre-process, %.1fms inference, %.1fms NMS per image at shape {(1, 3, *imgsz)}' % t)
# if sa7.5mszer(weights)  # update model (to fix SourceChangeWarning)

image 1/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1080.jpeg: 384x640 Done. (0.009s)
image 2/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1083.jpeg: 384x640 Done. (0.009s)
image 3/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1086.jpeg: 384x640 Done. (0.027s)
image 4/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1089.jpeg: 384x640 Done. (0.009s)
image 5/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1092.jpeg: 384x640 Done. (0.0

image 42/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1203.jpeg: 384x640 Done. (0.008s)
image 43/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1206.jpeg: 384x640 Done. (0.008s)
image 44/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1209.jpeg: 384x640 Done. (0.008s)
image 45/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1212.jpeg: 384x640 Done. (0.007s)
image 46/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1215.jpeg: 384x640 Done.

image 83/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1326.jpeg: 384x640 Done. (0.007s)
image 84/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1329.jpeg: 384x640 Done. (0.007s)
image 85/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1332.jpeg: 384x640 Done. (0.007s)
image 86/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1335.jpeg: 384x640 Done. (0.007s)
image 87/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1338.jpeg: 384x640 Done.

image 124/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1449.jpeg: 384x640 Done. (0.007s)
image 125/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1452.jpeg: 384x640 Done. (0.008s)
image 126/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1455.jpeg: 384x640 Done. (0.008s)
image 127/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1458.jpeg: 384x640 Done. (0.007s)
image 128/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1461.jpeg: 384x640 

image 165/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1572.jpeg: 384x640 Done. (0.008s)
image 166/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1575.jpeg: 384x640 Done. (0.007s)
image 167/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1578.jpeg: 384x640 Done. (0.007s)
image 168/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1581.jpeg: 384x640 Done. (0.007s)
image 169/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1584.jpeg: 384x640 

...

image 1272/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__546.jpeg: 384x640 Done. (0.007s)
image 1273/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__549.jpeg: 384x640 Done. (0.007s)
image 1274/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__552.jpeg: 384x640 Done. (0.007s)
image 1275/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__555.jpeg: 384x640 Done. (0.007s)
image 1276/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__558.jpeg: 384x640 

image 1313/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__657.jpeg: 384x640 Done. (0.007s)
image 1314/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__66.jpeg: 384x640 Done. (0.007s)
image 1315/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__660.jpeg: 384x640 Done. (0.007s)
image 1316/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__663.jpeg: 384x640 Done. (0.008s)
image 1317/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__666.jpeg: 384x640 D

image 1354/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__768.jpeg: 384x640 Done. (0.007s)
image 1355/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__771.jpeg: 384x640 Done. (0.007s)
image 1356/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__774.jpeg: 384x640 Done. (0.007s)
image 1357/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__777.jpeg: 384x640 Done. (0.007s)
image 1358/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__78.jpeg: 384x640 D

image 1395/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__879.jpeg: 384x640 Done. (0.008s)
image 1396/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__882.jpeg: 384x640 Done. (0.007s)
image 1397/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__885.jpeg: 384x640 Done. (0.007s)
image 1398/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__888.jpeg: 384x640 Done. (0.007s)
image 1399/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__891.jpeg: 384x640 

image 1436/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__99.jpeg: 384x640 Done. (0.008s)
image 1437/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__990.jpeg: 384x640 Done. (0.007s)
image 1438/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__993.jpeg: 384x640 Done. (0.007s)
image 1439/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__996.jpeg: 384x640 Done. (0.007s)
image 1440/1440 /home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_10__000078__999.jpeg: 384x640 D

In [4]:
preds

{'/home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1080.jpeg': [[[924.0,
    502.0,
    230.0,
    116.0],
   0.7438520193099976,
   '4'],
  [[1058.0, 534.5, 198.0, 109.0], 0.7716653347015381, '1'],
  [[243.5, 489.5, 149.0, 395.0], 0.7807810306549072, '0'],
  [[677.0, 453.0, 146.0, 280.0], 0.7846883535385132, '6'],
  [[304.0, 212.0, 244.0, 346.0], 0.7856239676475525, '7'],
  [[513.5, 444.5, 177.0, 335.0], 0.8634443879127502, '5'],
  [[618.0, 450.5, 138.0, 315.0], 0.8808950185775757, '2'],
  [[394.0, 476.0, 218.0, 294.0], 0.9062647819519043, '3']],
 '/home/user/Luxoft/animals_recognition/animals_detection/data/datasets/pigs_detection_dataset_yolo_masked_union_hard/images/validation/2019_12_02__000208__1083.jpeg': [[[1056.0,
    535.5,
    198.0,
    107.0],
   0.7620652318000793,
   '1'],
  [[922.0, 499.0, 230.0, 116.0], 0.7683718800544739, '4'],
  [[242.5, 481.0, 155.0, 410.0], 0.79

In [5]:
currnet_video_name = ""
pred_per_video = {}
for img_path in sorted(preds.keys()):
    video_name = '__'.join(img_path.split('/')[-1].split('__')[:2])
    if currnet_video_name != video_name:
        if currnet_video_name:
            pred_per_video[currnet_video_name] = frames
        currnet_video_name = video_name
        frames = []
    frames.append((img_path, preds[img_path]))
if currnet_video_name not in pred_per_video:
    pred_per_video[currnet_video_name] = frames
    

In [6]:
sys.path.insert(0, './deep_sort/')
from deep_sort.tracker import Tracker
from deep_sort.detection import Detection
from deep_sort.nn_matching import NearestNeighborDistanceMetric
from tools.generate_detections import create_box_encoder
from dataclasses import dataclass
import numpy as np

/home/user/anaconda3/envs/animals_detection/lib/python3.8/site-packages/sklearn/utils/linear_assignment_.py:18: FutureWarning: The linear_assignment_ module is deprecated in 0.21 and will be removed from 0.23. Use scipy.optimize.linear_sum_assignment instead.
  warnings.warn(
2022-06-23 22:25:43.641758: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/user/anaconda3/envs/animals_detection/lib/python3.8/site-packages/cv2/../../lib64:/usr/local/cuda-11.1/lib64:
2022-06-23 22:25:43.641784: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [7]:
encoder_path = 'deep_sort/mars-small128.pb'
feature_extractor = create_box_encoder(encoder_path)

2022-06-23 22:25:44.223929: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
2022-06-23 22:25:44.224079: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:982] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-06-23 22:25:44.224404: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
pciBusID: 0000:06:00.0 name: GeForce RTX 2080 computeCapability: 7.5
coreClock: 1.71GHz coreCount: 46 deviceMemorySize: 7.79GiB deviceMemoryBandwidth: 417.23GiB/s
2022-06-23 22:25:44.224485: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/user/anaconda3/envs/animals_detection/lib/python3.8/site-packages/cv2/../../lib64:/usr/local/cuda-11.1/l

In [15]:
@dataclass
class TrackedBox:
    x_min: int
    y_min: int
    x_max: int
    y_max: int
    score: float
    tracking_id: int
    class_name: str

    def __post_init__(self):
        self.width = self.x_max - self.x_min
        self.height = self.y_max - self.y_min
        self.bbox = (self.x_min, self.y_min, self.width, self.height)

class DeepsortTracker:

    def __init__(self, model_path: str, max_cosine_distance=0.7, nn_budget = None):
        self.encoder = create_box_encoder(model_path, batch_size=1)
        self.metric = NearestNeighborDistanceMetric("cosine", max_cosine_distance, nn_budget)
        self.tracker = Tracker(self.metric)

    def track_boxes(self, frame, boxes):
        """
        
        bbox - ((x_min, y_min, w, h), score, class_name)
        """
        features = np.array(self.encoder(frame, [box[0] for box in boxes]))

        detections = [
            Detection(bbox, score, feature, 'pig', class_name) 
            for (bbox, score, class_name), feature
            in zip(boxes,features)
            ]

        # Pass detections to the deepsort object and obtain the track information.
        self.tracker.predict()
        self.tracker.update(detections)

        # Obtain info from the tracks
        tracked_bboxes = []
        for track in self.tracker.tracks:
            if not track.is_confirmed() or track.time_since_update > 5:
                continue 
            bbox = track.detection.to_tlbr() # Get the corrected/predicted bounding box
            class_name = track.detection.class_name #Get the class name of particular object
            tracking_id = track.track_id # Get the ID for the particular track
            # index = key_list[val_list.index(class_name)] # Get predicted object index by object name

            x_min, y_min, x_max, y_max = [min(max(int(i), 0), 1700) for i in bbox.tolist()]


            det_obj = TrackedBox(
                x_min=x_min,
                y_min=y_min,
                x_max=x_max,
                y_max=y_max,
                score=track.detection.confidence,
                tracking_id=tracking_id,
                class_name = track.detection.activity
                )
            tracked_bboxes.append(det_obj) # Structure data, that we could use it with our draw_bbox function
        return tracked_bboxes
    
    def re_init(self):
        self.tracker = Tracker(self.metric)

In [16]:
tracker = DeepsortTracker(encoder_path)
pred_tracking_per_video = {}
for video_name, frames in pred_per_video.items():
    print(video_name)
    pred_tracking = []
    for frame in frames:
        img = cv2.imread(frame[0])
        pred_tracking.append(tracker.track_boxes(img, frame[1]))
    pred_tracking_per_video[video_name] = pred_tracking
    tracker.re_init()

2022-06-23 22:30:01.246374: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1257] Device interconnect StreamExecutor with strength 1 edge matrix:
2022-06-23 22:30:01.246409: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1263]      


2019_12_02__000208
2019_12_10__000060
2019_12_10__000078


In [17]:
pred_tracking_per_video

{'2019_12_02__000208': [[],
  [],
  [TrackedBox(x_min=924, y_min=502, x_max=1154, y_max=618, score=0.7438520193099976, tracking_id=1, class_name='4'),
   TrackedBox(x_min=1058, y_min=534, x_max=1256, y_max=643, score=0.7716653347015381, tracking_id=2, class_name='1'),
   TrackedBox(x_min=243, y_min=489, x_max=392, y_max=884, score=0.7807810306549072, tracking_id=3, class_name='0'),
   TrackedBox(x_min=677, y_min=453, x_max=823, y_max=733, score=0.7846883535385132, tracking_id=4, class_name='6'),
   TrackedBox(x_min=304, y_min=212, x_max=548, y_max=558, score=0.7856239676475525, tracking_id=5, class_name='7'),
   TrackedBox(x_min=513, y_min=444, x_max=690, y_max=779, score=0.8634443879127502, tracking_id=6, class_name='5'),
   TrackedBox(x_min=618, y_min=450, x_max=756, y_max=765, score=0.8808950185775757, tracking_id=7, class_name='2'),
   TrackedBox(x_min=394, y_min=476, x_max=612, y_max=770, score=0.9062647819519043, tracking_id=8, class_name='3')],
  [TrackedBox(x_min=924, y_min=502

In [53]:
for video_name, frames in pred_per_video.items():
    os.makedirs(os.path.join("TrackEval/data/gt/mot_challenge/animals-train", video_name, "gt"), exist_ok=True)
    with open(os.path.join("TrackEval/data/gt/mot_challenge/animals-train", video_name, "gt/gt.txt"), 'w') as f:
        for i, frame in enumerate(frames):
            if i < 2:
                continue
            ids = set()
            for box in frame[1]:
                if box[-1] in ids:
                    continue
                ids.update(box[-1])
                f.write(f"{i}, {box[-1]}, {', '.join(map(str, box[0]))}, -1, -1, -1, -1\n")
    with open(os.path.join("TrackEval/data/gt/mot_challenge/animals-train", video_name, "seqinfo.ini"), 'w') as f:
        f.write('[Sequence]\n')
        f.write(f"seqLength={len(frames)}")


In [54]:
for video_name, frames in pred_tracking_per_video.items():
    os.makedirs(os.path.join("TrackEval/data/trackers/mot_challenge/animals-train/data/data"), exist_ok=True)
    with open(os.path.join("TrackEval/data/trackers/mot_challenge/animals-train/data/data", f'{video_name}.txt'), 'w') as f:
        for i, frame in enumerate(frames):
            if not frame:
                continue
            for box in frame:
                f.write(f"{i}, {box.tracking_id}, {', '.join(map(str, box.bbox))}, -1, -1, -1, -1\n")
#                 <frame>, <id>, <bb_left>, <bb_top>, <bb_width>, <bb_height>, <conf>, <x>, <y>, <z>

In [32]:
pred_tracking_per_video

{'2019_12_02__000208': [[],
  [],
  [TrackedBox(x_min=924, y_min=502, x_max=1154, y_max=618, score=0.7438520193099976, tracking_id=1, class_name='4'),
   TrackedBox(x_min=1058, y_min=534, x_max=1256, y_max=643, score=0.7716653347015381, tracking_id=2, class_name='1'),
   TrackedBox(x_min=243, y_min=489, x_max=392, y_max=884, score=0.7807810306549072, tracking_id=3, class_name='0'),
   TrackedBox(x_min=677, y_min=453, x_max=823, y_max=733, score=0.7846883535385132, tracking_id=4, class_name='6'),
   TrackedBox(x_min=304, y_min=212, x_max=548, y_max=558, score=0.7856239676475525, tracking_id=5, class_name='7'),
   TrackedBox(x_min=513, y_min=444, x_max=690, y_max=779, score=0.8634443879127502, tracking_id=6, class_name='5'),
   TrackedBox(x_min=618, y_min=450, x_max=756, y_max=765, score=0.8808950185775757, tracking_id=7, class_name='2'),
   TrackedBox(x_min=394, y_min=476, x_max=612, y_max=770, score=0.9062647819519043, tracking_id=8, class_name='3')],
  [TrackedBox(x_min=924, y_min=502